In [116]:
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
import numpy as np
import statsmodels.api as sm
from statsmodels.stats.outliers_influence import variance_inflation_factor
import statsmodels.formula.api as smf
from scipy.linalg import sqrtm
pd.options.plotting.backend = "plotly"


# Read Data and preprocessing


## 機構評等


In [2]:
df_rating = pd.read_csv("./data/rating.csv",
                        index_col=0)[['日期',
                                      '股票代號',
                                      '股票名稱',
                                      '券商代號',
                                      '券商名稱',
                                      '投資評等',
                                      '目標價']].drop_duplicates()


/var/folders/xq/syr6491s2dz4hc1nq8wg29hm0000gn/T/ipykernel_35443/696216106.py:1: DtypeWarning: Columns (17,18) have mixed types. Specify dtype option on import or set low_memory=False.
  df_rating = pd.read_csv("./data/rating.csv",


In [3]:
df_rating['日期'] = pd.to_datetime(df_rating['日期'], format='%Y/%m/%d')
df_rating['股票代號'] = df_rating['股票代號'].astype(pd.StringDtype())
df_rating = df_rating.convert_dtypes().sort_values(
    by=['日期']).reset_index(
        drop=True)
df_rating.head(20)


日期  股票代號 股票名稱   券商代號     券商名稱         投資評等    目標價
0  2008-01-23  2002   中鋼  C0073     富邦證券         增加持股   49.0
1  2008-02-12  2303   聯電  C0086     群益證券           中立   17.9
2  2008-02-12  2454  聯發科  C0073     富邦證券         增加持股  484.0
3  2008-02-12  3037   欣興  C0086     群益證券           買進   50.6
4  2008-02-12  3037   欣興  C0020     元京證券           持有   48.0
5  2008-02-12  2454  聯發科  C0086     群益證券           中立  357.0
6  2008-02-13  2330  台積電  C0070    麥格理證券   Outperform   68.0
7  2008-02-20  2330  台積電  C0020     元京證券           買進   65.0
8  2008-02-20  2454  聯發科  C0020     元京證券           持有  384.0
9  2008-02-20  2382   廣達  C0073     富邦證券           中立   37.0
10 2008-02-21  2327   國巨  C0070    麥格理證券   Outperform   13.8
11 2008-02-26  2357   華碩  C0090  摩根士丹利證券  Over weight  104.0
12 2008-02-26  2327   國巨  C0020     元京證券           賣出    7.7
13 2008-02-26  2382   廣達  C0090  摩根士丹利證券           EW   40.0
14 2008-02-26  2327   國巨  C0086     群益證券           中立   10.0
15 2008-02-27  2002   中鋼  C0073     富邦證券         增加持股   49.0
16 2008-03-05  2892  第一金  C0086     群益證券           買進   36.0
17 2008-03-10  2454  聯發科  C0020     元京證券           持有  368.0
18 2008-03-21  2303   聯電  C0020     元京證券           持有   15.6
19 2008-03-28  2412  中華電  C0020     元京證券           買進   95.0

## 日資料


In [4]:
df_Daily = pd.read_csv("./data/Daily.csv")
df_Daily['日期'] = pd.to_datetime(df_Daily['日期'], format='%Y/%m/%d')
df_Daily["股票代號"] = df_Daily["股票代號"].astype(pd.StringDtype())
df_Daily['本益比'] = df_Daily['本益比'].replace(
    "- -", pd.NA).astype(pd.Float64Dtype())
df_Daily = df_Daily.convert_dtypes()
df_Daily.sort_values(by=['日期'], inplace=True)
df_Daily.reset_index(drop=True, inplace=True)


In [5]:
df_Daily


日期  股票代號 股票名稱  總市值(億)      最高價      最低價      收盤價   本益比  股價淨值比   
0      2008-01-02  9910   豐泰   126.0     7.96      7.8      7.8  10.3   1.67  \
1      2008-01-02  2408   南科   844.8   367.17   353.43   353.43  <NA>   1.29   
2      2008-01-02  2395   研華   349.0    28.04    27.31    27.31  11.4   2.49   
3      2008-01-02  2382   廣達  1565.6    17.27    16.82    16.84   8.4   1.79   
4      2008-01-02  2379   瑞昱   518.1     53.6    50.61    52.68  11.4   3.14   
...           ...   ...  ...     ...      ...      ...      ...   ...    ...   
176367 2022-12-30  2883  開發金  2321.9     12.7     12.6     12.6   8.9   1.11   
176368 2022-12-30  2882  國泰金  6481.0    40.25     39.6     40.0   9.7   1.87   
176369 2022-12-30  2881  富邦金  7879.3     56.8     56.2     56.3   8.7   1.43   
176370 2022-12-30  3008  大立光  2723.4  2043.57  1999.46  1999.46  11.6    1.8   
176371 2022-12-30  1101   台泥  2475.3     34.0    33.65    33.65  42.7   1.16   

        週轉率(%)  
0         0.08  
1         0.32  
2          0.3  
3         0.23  
4         2.77  
...        ...  
176367    0.06  
176368    0.63  
176369    0.04  
176370    0.24  
176371    0.12  

[176372 rows x 10 columns]

## 外資持股比例


In [6]:
df_holding = pd.read_csv("./data/外資持股.csv", index_col=0)
df_holding['日期'] = pd.to_datetime(df_holding['日期'], format='%Y/%m/%d')
df_holding['股票代號'] = df_holding['股票代號'].astype(pd.StringDtype())
df_holding = df_holding.convert_dtypes().sort_values(by='日期', ascending=True)
df_holding['外資持股比率(%)'] = (df_holding['外資持股比率(%)'] / 100)
df_holding.rename(columns={'外資持股比率(%)': '外資持股比率'}, inplace=True)
df_holding.reset_index(drop=True, inplace=True)


In [7]:
df_holding.head(20)


日期  股票代號 股票名稱  外資持股比率
0  2008-01-02  9910   豐泰  0.0625
1  2008-01-02  2408   南科  0.0661
2  2008-01-02  2395   研華  0.3359
3  2008-01-02  2382   廣達  0.1981
4  2008-01-02  2379   瑞昱  0.2076
5  2008-01-02  2357   華碩  0.3789
6  2008-01-02  2330  台積電  0.7179
7  2008-01-02  2327   國巨  0.4295
8  2008-01-02  2317   鴻海  0.5649
9  2008-01-02  2308  台達電  0.7382
10 2008-01-02  2303   聯電  0.4382
11 2008-01-02  2207  和泰車  0.2319
12 2008-01-02  2002   中鋼  0.3226
13 2008-01-02  1605   華新  0.2977
14 2008-01-02  1402   遠紡  0.3434
15 2008-01-02  1326   臺化  0.3147
16 2008-01-02  1303   南亞  0.2447
17 2008-01-02  1301   臺塑  0.3751
18 2008-01-02  1216   統一  0.4085
19 2008-01-02  1101   台泥  0.4932

## 上市日期


In [8]:
in_market = pd.read_excel("./data/上市日期.xlsx", index_col=0)
in_market.index = in_market.index.astype(str)
in_market


股票名稱       上市日期
股票代號                   
2207     和泰車 1997-02-25
2379      瑞昱 1998-10-26
2395      研華 1999-12-13
2603      長榮 1987-09-21
2609      陽明 1992-04-20
2615      萬海 1996-05-16
2883     開發金 2001-12-28
2884     玉山金 2002-01-28
2887     台新金 2002-02-18
2890     永豐金 2002-05-09
3034      聯詠 2002-08-26
3037      欣興 2002-08-26
5876    上海商銀 2018-10-19
6415  矽力*-KY 2013-12-12
9910      豐泰 1992-02-18

# 計算預測誤差


## 預測誤差敘述性統計

目標價在不同預測期間的誤差


In [9]:
periods = list(map(lambda D: pd.Timedelta(D, "d"), [30, 60, 90, 180, 360]))


In [10]:
df_rating.head(10)


日期  股票代號 股票名稱   券商代號   券商名稱        投資評等    目標價
0 2008-01-23  2002   中鋼  C0073   富邦證券        增加持股   49.0
1 2008-02-12  2303   聯電  C0086   群益證券          中立   17.9
2 2008-02-12  2454  聯發科  C0073   富邦證券        增加持股  484.0
3 2008-02-12  3037   欣興  C0086   群益證券          買進   50.6
4 2008-02-12  3037   欣興  C0020   元京證券          持有   48.0
5 2008-02-12  2454  聯發科  C0086   群益證券          中立  357.0
6 2008-02-13  2330  台積電  C0070  麥格理證券  Outperform   68.0
7 2008-02-20  2330  台積電  C0020   元京證券          買進   65.0
8 2008-02-20  2454  聯發科  C0020   元京證券          持有  384.0
9 2008-02-20  2382   廣達  C0073   富邦證券          中立   37.0

In [11]:
df_Daily.head(10)


日期  股票代號 股票名稱   總市值(億)     最高價     最低價     收盤價   本益比  股價淨值比  週轉率(%)
0 2008-01-02  9910   豐泰    126.0    7.96     7.8     7.8  10.3   1.67    0.08
1 2008-01-02  2408   南科    844.8  367.17  353.43  353.43  <NA>   1.29    0.32
2 2008-01-02  2395   研華    349.0   28.04   27.31   27.31  11.4   2.49     0.3
3 2008-01-02  2382   廣達   1565.6   17.27   16.82   16.84   8.4   1.79    0.23
4 2008-01-02  2379   瑞昱    518.1    53.6   50.61   52.68  11.4   3.14    2.77
5 2008-01-02  2357   華碩   3616.5  129.17   125.4  126.05  10.5   2.25    0.41
6 2008-01-02  2330  台積電  15988.4   35.55   34.52   34.69  13.7   3.53    0.15
7 2008-01-02  2327   國巨    268.2   27.42   26.35   26.35   4.8   0.84    0.46
8 2008-01-02  2317   鴻海  12235.6   61.45   59.17   59.17  12.3   3.49    0.19
9 2008-01-02  2308  台達電   2243.3    60.5   58.58   58.58  12.0   3.75    0.16

## 合併機構預測與當日股價資料集


In [12]:
df_rating_daily = df_rating.merge(
    df_Daily, how='left', on=[
        '日期', '股票代號', '股票名稱'])


In [13]:
df_tp = df_rating_daily[['日期', '券商代號', '券商名稱',
                         '目標價', '收盤價', '股票代號', '股票名稱']].copy()


In [14]:
df_tp['多/空'] = df_tp['目標價'] > df_tp['收盤價']


In [15]:
df_tp.dropna(inplace=True)
df_tp


日期   券商代號    券商名稱     目標價     收盤價  股票代號    股票名稱   多/空
0     2008-01-23  C0073    富邦證券    49.0   18.67  2002      中鋼  True
1     2008-02-12  C0086    群益證券    17.9    8.75  2303      聯電  True
2     2008-02-12  C0073    富邦證券   484.0  138.86  2454     聯發科  True
3     2008-02-12  C0086    群益證券    50.6   24.93  3037      欣興  True
4     2008-02-12  C0020    元京證券    48.0   24.93  3037      欣興  True
...          ...    ...     ...     ...     ...   ...     ...   ...
29090 2022-12-29  C0019    元大投顧   185.0   121.5  3037      欣興  True
29091 2022-12-29  C0019    元大投顧   353.0   281.0  2308     台達電  True
29092 2022-12-30  C0049  花旗美邦證券   550.0  446.09  2330     台積電  True
29093 2022-12-30  C0006      大和   320.0   286.5  2308     台達電  True
29094 2022-12-30  C0006      大和  1200.0   931.0  1590  亞德客-KY  True

[28210 rows x 8 columns]

## 未來一段時間股價極值


In [16]:
df_daily_min_max = df_Daily[['日期', '股票代號', '最高價', '最低價']].pivot(
    index='日期', columns='股票代號', values=['最高價', '最低價'])
df_daily_max = df_daily_min_max.groupby(axis=1, level=0).get_group(
    '最高價').resample('1D').first().fillna(method='ffill')
rolling_maxs = [df_daily_max.rolling(period.days).max(
).shift(-period.days).stack().reset_index() for period in periods]
df_daily_min = df_daily_min_max.groupby(axis=1, level=0).get_group(
    '最低價').resample('1D').first().fillna(method='ffill')
rolling_mins = [df_daily_min.rolling(period.days).min(
).shift(-period.days).stack().reset_index() for period in periods]


In [17]:
rolling_maxs[0]


日期  股票代號     最高價
0      2008-01-02  1101   19.30
1      2008-01-02  1216   18.30
2      2008-01-02  1301   45.05
3      2008-01-02  1303   42.43
4      2008-01-02  1326   40.07
...           ...   ...     ...
259942 2022-11-30  5876   49.80
259943 2022-11-30  5880   26.75
259944 2022-11-30  6415  573.92
259945 2022-11-30  6505   85.50
259946 2022-11-30  9910  223.00

[259947 rows x 3 columns]

## 股價動能


In [18]:
period = pd.Timedelta(360, "d")


In [19]:
# 30day return for momentum
momentum = df_Daily[['日期', '股票代號', '收盤價']].pivot(
    index='日期', columns='股票代號', values=['收盤價'])
momentum = (momentum.shift(period.days) / momentum - 1)
momentum = momentum.stack().reset_index()[['日期', '股票代號', '收盤價']]
momentum.rename(columns={'收盤價': f'{period.days}日報酬率'}, inplace=True)
momentum.dropna(inplace=True)


In [20]:
momentum


日期  股票代號   360日報酬率
0      2009-06-18  1101  0.439183
1      2009-06-18  1216  0.157475
2      2009-06-18  1301  0.341115
3      2009-06-18  1303  0.739955
4      2009-06-18  1326  0.476721
...           ...   ...       ...
158218 2022-12-30  5876 -0.059251
158219 2022-12-30  5880 -0.268077
158220 2022-12-30  6415  1.221716
158221 2022-12-30  6505  0.188294
158222 2022-12-30  9910  0.056707

[158223 rows x 3 columns]

## 合併股價動能到資料集


In [21]:
df_rating_daily_momentum = df_rating_daily.merge(
    momentum, how='left', on=['日期', '股票代號']).dropna()


In [22]:
df_rating_daily_momentum.head(10)


日期  股票代號 股票名稱   券商代號   券商名稱        投資評等    目標價  總市值(億)     最高價   
1353 2009-06-19  2454  聯發科  C0089  德意志證券        Sell  223.0  4067.4  207.12  \
1354 2009-06-19  3034   聯詠  C0073   富邦證券        增加持股   85.0   433.3   30.56   
1355 2009-06-22  1402   遠紡  C0060   高盛證券         Buy   41.1  1748.0   18.19   
1356 2009-06-22  2382   廣達  C0048   法銀巴黎        Hold   53.0  1928.1   22.11   
1357 2009-06-22  2379   瑞昱  C0040   里昂證券  Outperform   62.0   276.5   29.05   
1358 2009-06-22  2887  台新金  C0034    永豐金          買進   14.5   807.1    4.35   
1360 2009-06-22  3034   聯詠  C0070  麥格理證券  Outperform   90.0   436.3   31.02   
1361 2009-06-23  2454  聯發科  C0086   群益證券          買進  438.0  4024.5  206.02   
1362 2009-06-24  2912  統一超  C0086   群益證券          中立   79.0   776.1    47.8   
1363 2009-06-24  2454  聯發科  C0089  德意志證券        Sell  223.0  4147.9  215.84   

         最低價     收盤價   本益比  股價淨值比  週轉率(%)   360日報酬率  
1353  198.94  206.57  15.5   4.55    0.81 -0.048361  
1354    29.2   30.56  15.9   2.29    1.88  0.385144  
1355   17.12   18.19  24.2    2.0    0.97 -0.047828  
1356   21.41   22.11  10.4    2.1    0.41 -0.263229  
1357   28.17   28.85  20.0   1.75    2.81  0.658579  
1358    4.18    4.26  25.7   0.95    1.07  0.152582  
1360   29.99   30.77  16.1   2.31    1.51  0.346766  
1361  204.39  204.39  15.3    4.5    0.45 -0.157836  
1362   46.14   47.14  20.6   4.48    0.32 -0.056216  
1363  205.48  210.66  15.8   4.64    0.87 -0.225957

## 計算誤差


In [23]:
def calc_error(x):
    # if(x['日期'] == pd.to_datetime("2020-10-07")):
    #     print(x)
    return x['目標價'] / x['最高價'] - 1 if x['多/空'] else 1 - x['目標價'] / x['最低價']


In [24]:
tp_errors = {}
for i, p in enumerate(periods):
    df_tmp = df_tp.copy()
    df_tmp['日期'] = df_tmp['日期'] + p
    df_tmp = df_tmp.merge(
        rolling_maxs[i], how='left', on=[
            '日期', '股票代號']).merge(
        rolling_mins[i], how='left', on=[
            '日期', '股票代號'])
    tp_errors[f'{p.days}天後誤差'] = np.array(
        df_tmp.apply(func=calc_error, axis=1))
for k, v in tp_errors.items():
    df_tp[k] = v


In [25]:
df_tp.dropna(inplace=True)


In [26]:
df_tp.head(10)


日期   券商代號   券商名稱    目標價     收盤價  股票代號 股票名稱   多/空    30天後誤差   
0 2008-01-23  C0073   富邦證券   49.0   18.67  2002   中鋼  True  1.259106  \
1 2008-02-12  C0086   群益證券   17.9    8.75  2303   聯電  True  0.768775   
2 2008-02-12  C0073   富邦證券  484.0  138.86  2454  聯發科  True  1.261999   
3 2008-02-12  C0086   群益證券   50.6   24.93  3037   欣興  True  0.740028   
4 2008-02-12  C0020   元京證券   48.0   24.93  3037   欣興  True  0.650619   
5 2008-02-12  C0086   群益證券  357.0  138.86  2454  聯發科  True  0.668458   
6 2008-02-13  C0070  麥格理證券   68.0   34.35  2330  台積電  True  0.711122   
7 2008-02-20  C0020   元京證券   65.0   35.03  2330  台積電  True  0.635632   
8 2008-02-20  C0020   元京證券  384.0  165.83  2454  聯發科  True  0.713903   
9 2008-02-20  C0073   富邦證券   37.0   14.65  2382   廣達  True  1.016349   

     60天後誤差    90天後誤差   180天後誤差   360天後誤差  
0  1.001634  1.001634  1.163355  1.520576  
1  0.708015  0.708015  1.277354  0.645221  
2  1.160232  1.254098  1.336810  0.455114  
3  0.698557  0.713512  1.014331  0.542213  
4  0.611279  0.625466  0.910828  0.462969  
5  0.593394  0.662630  0.723638  0.073297  
6  0.699150  0.699150  0.797515  0.614435  
7  0.624188  0.645153  0.749193  0.543210  
8  0.788376  0.842434  0.863897  0.154471  
9  0.864919  0.801363  0.794374  0.114794

In [27]:
df_tp[[f'{p.days}天後誤差' for p in periods]].abs().describe()


30天後誤差        60天後誤差        90天後誤差       180天後誤差       360天後誤差
count  22406.000000  22406.000000  22406.000000  22406.000000  22406.000000
mean       0.592775      0.555903      0.534757      0.474918      0.427067
std        0.547967      0.543551      0.539159      0.464238      0.396835
min        0.000000      0.000000      0.000000      0.000000      0.000054
25%        0.233266      0.202259      0.188912      0.167437      0.147738
50%        0.448749      0.409605      0.387847      0.341629      0.317637
75%        0.780659      0.731333      0.702976      0.632221      0.584607
max       12.164310     11.646370     11.646370     11.765957     11.844910

In [28]:
df_tp[[f'{p.days}天後誤差' for p in periods]].hist()


In [30]:
df_tp[['360天後誤差']].abs().hist()

In [29]:
df_tp[df_tp['360天後誤差'].abs() >= df_tp['360天後誤差'].abs().max()]


日期   券商代號  券商名稱    目標價    收盤價  股票代號 股票名稱   多/空    30天後誤差   
18227 2018-11-05  C0067  統一證券  270.0  20.39  2002   中鋼  True  12.16431  \

         60天後誤差    90天後誤差    180天後誤差   360天後誤差  
18227  11.64637  11.64637  11.765957  11.84491

## 結論


券商的目標價在預測 360 天後的股價有較高的準確率 \
故此研究以 360 天作為計算預測誤差的期間


# 驗證假說


## 假說一：外資券商對於目標價預測誤差優於本土券商


In [84]:
# 是否為本土券商
domestic = {
    '富邦證券',
    '群益證券',
    '元京證券',
    '凱基證券',
    '元富證券投顧',
    '統一證券',
    '日盛證券',
    '元大投顧',
    '永豐金',
    '中國信託綜合證券',
    '群益證券',
    '兆豐',
    '國票',
    '國泰',
    '第一金證券',
    '台新投顧',
    '元京證券',
    '宏遠證券',
    '大華證券',
    '康和證券',
    '玉山證券',
    '台工銀',
    '大和國泰證券',
    '奔亞投顧',
    '金鼎證券',
    '合作金庫證券',
    '華南永昌',
    '凱基'}


In [85]:
in_domestic = df_tp['券商名稱'].apply(
    lambda x: float(
        x in domestic)).rename('是否為本土券商')


In [86]:
df_implied_ret = (
    df_rating_daily_momentum['目標價'] /
    df_rating_daily_momentum['收盤價'] -
    1).rename("隱含報酬率")


In [87]:
df_reg1 = pd.concat([df_rating_daily_momentum, in_domestic, df_tp['360天後誤差'], df_implied_ret], axis=1)[
    ['360天後誤差', '360日報酬率', '總市值(億)', '本益比', '股價淨值比', '是否為本土券商', '週轉率(%)', "隱含報酬率"]].dropna()

In [88]:
df_reg1.columns = [
    'tp_error',
    'momentum',
    'Size',
    'PE',
    'PB',
    'Domestic',
    'turnover',
    'implied_ret']
df_reg1.head(10)


tp_error  momentum    Size    PE    PB  Domestic  turnover  implied_ret
1353 -0.250722 -0.048361  4067.4  15.5  4.55       0.0      0.81     0.079537
1354  0.774160  0.385144   433.3  15.9  2.29       1.0      1.88     1.781414
1355  0.503842 -0.047828  1748.0  24.2   2.0       0.0      0.97     1.259483
1356  0.624770 -0.263229  1928.1  10.4   2.1       0.0      0.41     1.397105
1357  0.514042  0.658579   276.5  20.0  1.75       0.0      2.81     1.149047
1358  1.077364  0.152582   807.1  25.7  0.95       1.0      1.07     2.403756
1360  0.878522  0.346766   436.3  16.1  2.31       0.0      1.51     1.924927
1361  0.471675 -0.157836  4024.5  15.3   4.5       1.0      0.45     1.142962
1362 -0.311967 -0.056216   776.1  20.6  4.48       1.0      0.32     0.675859
1363 -0.250722 -0.225957  4147.9  15.8  4.64       0.0      0.87     0.058578

In [89]:
df_reg1 = df_reg1[df_reg1['tp_error'] <11]

In [90]:
model1 = smf.ols(
    "np.abs(tp_error) ~ np.log(Size) + PE + PB + Domestic + turnover + momentum + implied_ret",
    data=df_reg1.astype(
        np.float64))


In [91]:
results1 = model1.fit(cov_type="HC0")
results1.summary()


<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:       np.abs(tp_error)   R-squared:                       0.316
Model:                            OLS   Adj. R-squared:                  0.316
Method:                 Least Squares   F-statistic:                     402.1
Date:                Sat, 10 Jun 2023   Prob (F-statistic):               0.00
Time:                        15:21:44   Log-Likelihood:                -5413.5
No. Observations:               20749   AIC:                         1.084e+04
Df Residuals:                   20741   BIC:                         1.091e+04
Df Model:                           7                                         
Covariance Type:                  HC0                                         
================================================================================
                   coef    std err          z      P>|z|      [0.025      0.975]
--------------------------------------------------------------------------------
Intercept        0.3226      0.021     15.334      0.000       0.281       0.364
np.log(Size)    -0.0175      0.002     -8.287      0.000      -0.022      -0.013
PE               0.0001   7.68e-05      1.601      0.109   -2.76e-05       0.000
PB              -0.0139      0.002     -7.288      0.000      -0.018      -0.010
Domestic         0.0120      0.004      2.713      0.007       0.003       0.021
turnover         0.0404      0.003     12.802      0.000       0.034       0.047
momentum        -0.1618      0.009    -17.119      0.000      -0.180      -0.143
implied_ret      0.3459      0.009     38.170      0.000       0.328       0.364
==============================================================================
Omnibus:                     4352.454   Durbin-Watson:                   1.297
Prob(Omnibus):                  0.000   Jarque-Bera (JB):            20936.639
Skew:                           0.941   Prob(JB):                         0.00
Kurtosis:                       7.547   Cond. No.                         313.
==============================================================================

Notes:
[1] Standard Errors are heteroscedasticity robust (HC0)
"""

In [92]:
results1.t_test("Domestic = 0")


<class 'statsmodels.stats.contrast.ContrastResults'>
                             Test for Constraints                             
                 coef    std err          z      P>|z|      [0.025      0.975]
------------------------------------------------------------------------------
c0             0.0120      0.004      2.713      0.007       0.003       0.021

In [93]:
fig = px.imshow(df_reg1[df_reg1.columns[1:]].corr(),text_auto=True ,width=800,height=800)
fig.update_traces(textfont_size=12)

In [94]:
pd.Series([variance_inflation_factor(df_reg1[df_reg1.columns[1:]].astype(float), i)
           for i in range(len(df_reg1.columns[1:]))], index=df_reg1.columns[1:])


momentum       1.493478
Size           1.233642
PE             1.261602
PB             2.363701
Domestic       1.747255
turnover       1.443569
implied_ret    1.718445
dtype: float64

In [95]:
df_reg1["tp_error"] = df_reg1["tp_error"].abs()
fig = px.scatter(df_reg1,x="Domestic",y="tp_error")
fig.add_trace(go.Scatter(x=[0,1],y=[0.3003,0.3003+0.0123],name="reg"))
fig.update_xaxes(nticks=2)
fig.update_layout(width=500,title="假說一")

In [96]:
# epsilon
(results1.predict() - df_reg1['tp_error']).mean()

-2.4656165104210908e-17

In [97]:
df_reg1[df_reg1.columns[1:]].mul((results1.predict() - df_reg1['tp_error']),axis=0).mean(axis=0)

momentum            -0.0
Size          -64.955092
PE                  -0.0
PB                   0.0
Domestic             0.0
turnover             0.0
implied_ret         -0.0
dtype: object

In [98]:
df_reg1['Size'].apply(np.log).mul((results1.predict() - df_reg1['tp_error'])).mean()

-2.301242076393018e-16

## 假說二：台灣五十成分股中的公司，券商預測能力越準確（預測誤差愈小）


這裡選用:

- 玉山金 (臺證所：2884)
- 臺新金 (臺證所：2887)
- 研華（臺證所：2395）
- 上海商銀(臺證所：5876)
- 和泰汽車(臺證所：2207)
- 豐泰企業（臺證所：9910）
- 瑞昱半導體（臺證所：2379）
- 矽力-KY（臺證所：6415）
- 聯詠科技（臺證所：3034）
- 長榮海運（臺證所：2603）
- 陽明海運（臺證所：2609）
- 萬海航運（臺證所：2615）
- 欣興電子（臺證所：3037）
- 永豐金融控股（臺證所：2890）


In [75]:
add_in_50 = {
    "2884",
    "4938",
    "2395",
    "5876",
    "2207",
    "9910",
    "2379",
    "6415",
    "3034",
    "2603",
    "2609",
    "2615",
    "3037",
    "2890"}


當月第三個禮拜五之下一個交易日生效


In [76]:
add_in_date = {
    "2884": "2013-06-24",
    "4938": "2013-06-24",
    "2395": "2014-06-23",
    "5876": "2018-12-24",
    "2207": "2019-03-24",
    "9910":"2019-06-24",
    "2379":"2020-09-24",
    "6415":"2020-09-24",
    "3034":"2020-12-24",
    "2603":"2021-06-24",
    "2609":"2021-06-24",
    "2615":"2021-06-24",
    "3037":"2021-12-24",
    "2890":"2022-09-24"
}
add_in_date = pd.to_datetime(pd.Series(add_in_date))

In [77]:
add_in_date

2884   2013-06-24
4938   2013-06-24
2395   2014-06-23
5876   2018-12-24
2207   2019-03-24
9910   2019-06-24
2379   2020-09-24
6415   2020-09-24
3034   2020-12-24
2603   2021-06-24
2609   2021-06-24
2615   2021-06-24
3037   2021-12-24
2890   2022-09-24
dtype: datetime64[ns]

### 計算到上市日期的天數

In [78]:
in_market['上市日期']


股票代號
2207   1997-02-25
2379   1998-10-26
2395   1999-12-13
2603   1987-09-21
2609   1992-04-20
2615   1996-05-16
2883   2001-12-28
2884   2002-01-28
2887   2002-02-18
2890   2002-05-09
3034   2002-08-26
3037   2002-08-26
5876   2018-10-19
6415   2013-12-12
9910   1992-02-18
Name: 上市日期, dtype: datetime64[ns]

In [79]:
df_reg2 = df_rating_daily_momentum[df_rating_daily_momentum["股票代號"].apply(
    lambda x: x in add_in_50)]


In [80]:
df_reg2.head(3)


日期  股票代號 股票名稱   券商代號   券商名稱        投資評等   目標價  總市值(億)    最高價   
1354 2009-06-19  3034   聯詠  C0073   富邦證券        增加持股  85.0   433.3  30.56  \
1357 2009-06-22  2379   瑞昱  C0040   里昂證券  Outperform  62.0   276.5  29.05   
1360 2009-06-22  3034   聯詠  C0070  麥格理證券  Outperform  90.0   436.3  31.02   

        最低價    收盤價   本益比  股價淨值比  週轉率(%)   360日報酬率  
1354   29.2  30.56  15.9   2.29    1.88  0.385144  
1357  28.17  28.85  20.0   1.75    2.81  0.658579  
1360  29.99  30.77  16.1   2.31    1.51  0.346766

In [81]:
days = df_reg2['日期'].reset_index()['日期'] - \
    in_market['上市日期'][df_reg2['股票代號']].reset_index()['上市日期']
days = days.apply(lambda x: x.days)
days.index = df_reg2.index


In [82]:
df_reg2.loc[:, '上市至報告發布天數'] = days

/var/folders/xq/syr6491s2dz4hc1nq8wg29hm0000gn/T/ipykernel_76280/3213433164.py:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



### 計算是否為台灣50成分股

In [83]:
df_reg2.loc[:,'是否台灣50'] = df_reg2.apply(lambda x: x['日期'] > add_in_date[x['股票代號']],axis=1).astype(float)

/var/folders/xq/syr6491s2dz4hc1nq8wg29hm0000gn/T/ipykernel_76280/2613556164.py:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [84]:
df_reg2.head(3)

日期  股票代號 股票名稱   券商代號   券商名稱        投資評等   目標價  總市值(億)    最高價   
1354 2009-06-19  3034   聯詠  C0073   富邦證券        增加持股  85.0   433.3  30.56  \
1357 2009-06-22  2379   瑞昱  C0040   里昂證券  Outperform  62.0   276.5  29.05   
1360 2009-06-22  3034   聯詠  C0070  麥格理證券  Outperform  90.0   436.3  31.02   

        最低價    收盤價   本益比  股價淨值比  週轉率(%)   360日報酬率  上市至報告發布天數  是否台灣50  
1354   29.2  30.56  15.9   2.29    1.88  0.385144       2489     0.0  
1357  28.17  28.85  20.0   1.75    2.81  0.658579       3892     0.0  
1360  29.99  30.77  16.1   2.31    1.51  0.346766       2492     0.0

In [85]:
df_reg2 = df_reg2.merge(df_tp[["日期","股票代號","券商代號","券商名稱","360天後誤差"]],how='left',on=["日期","股票代號","券商代號","券商名稱"])

In [86]:
df_reg2["隱含報酬率"] = df_reg2.apply(lambda x: x["目標價"]/x["收盤價"] - 1,axis=1)

In [87]:
# df_reg2 = df_reg2[['360天後誤差', '360日報酬率', '總市值(億)', '本益比', 
#                    '股價淨值比','週轉率(%)',"隱含報酬率","上市至報告發布天數","是否台灣50"]].dropna()

In [88]:
df_reg2 = df_reg2[['360天後誤差', '360日報酬率', '本益比', 
                   '股價淨值比','週轉率(%)',"隱含報酬率","上市至報告發布天數","是否台灣50"]].dropna()

In [89]:
df_reg2.columns = [
    'tp_error',
    'momentum',
    # 'Size',
    'PE',
    'PB',
    'turnover',
    'implied_ret',
    "days",
    "is_fifty"]

In [90]:
df_reg2

tp_error  momentum    PE    PB  turnover  implied_ret  days  is_fifty
0     0.774160  0.385144  15.9  2.29      1.88     1.781414  2489       0.0
1     0.514042  0.658579  20.0  1.75      2.81     1.149047  3892       0.0
2     0.878522  0.346766  16.1  2.31      1.51     1.924927  2492       0.0
3    -0.161758   0.99177  18.9  0.94      0.53     1.175191  2499       0.0
4     0.358074   0.68073  33.2  0.81      0.14    -0.221095  7952       0.0
...        ...       ...   ...   ...       ...          ...   ...       ...
4125 -0.204297 -0.563249  16.3  5.48      0.67     0.246969  6707       1.0
4126  0.016732 -0.568552  17.4  5.85      2.21     0.491666  6708       1.0
4127 -0.018633 -0.555343  17.2  5.76      1.39     0.462643  6709       1.0
4128 -0.174112 -0.468743  20.0  6.93      0.71     0.229050  8110       1.0
4129 -0.173807 -0.096654  15.8  1.77      0.26     0.254647  6920       1.0

[4130 rows x 8 columns]

In [ ]:
# model2 = smf.ols("np.abs(tp_error) ~ np.log(Size) + PE + PB + momentum + turnover + implied_ret + days + is_fifty + days*is_fifty",data=df_reg2.astype(np.float64))

In [92]:
model2 = smf.ols("np.abs(tp_error) ~  PE + PB + momentum + turnover + implied_ret + days + is_fifty + days*is_fifty",data=df_reg2.astype(np.float64))

In [93]:
result2 = model2.fit(cov_type="HC0")
result2.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:       np.abs(tp_error)   R-squared:                       0.324
Model:                            OLS   Adj. R-squared:                  0.323
Method:                 Least Squares   F-statistic:                     155.7
Date:                Sun, 28 May 2023   Prob (F-statistic):          7.78e-230
Time:                        22:42:01   Log-Likelihood:                -1711.1
No. Observations:                4130   AIC:                             3440.
Df Residuals:                    4121   BIC:                             3497.
Df Model:                           8                                         
Covariance Type:                  HC0                                         
=================================================================================
                    coef    std err          z      P>|z|      [0.025      0.975]
---------------------------------------------------------------------------------
Intercept         0.3103      0.034      9.017      0.000       0.243       0.378
PE            -4.581e-05   2.66e-05     -1.724      0.085   -9.79e-05    6.28e-06
PB               -0.0446      0.003    -14.732      0.000      -0.051      -0.039
momentum         -0.3522      0.023    -15.616      0.000      -0.396      -0.308
turnover          0.0032      0.005      0.666      0.505      -0.006       0.012
implied_ret       0.2742      0.018     15.128      0.000       0.239       0.310
days           7.794e-06   4.55e-06      1.714      0.086   -1.12e-06    1.67e-05
is_fifty         -0.1290      0.041     -3.133      0.002      -0.210      -0.048
days:is_fifty  1.137e-05   6.09e-06      1.869      0.062   -5.56e-07    2.33e-05
==============================================================================
Omnibus:                      507.027   Durbin-Watson:                   1.105
Prob(Omnibus):                  0.000   Jarque-Bera (JB):             1894.737
Skew:                           0.579   Prob(JB):                         0.00
Kurtosis:                       6.110   Cond. No.                     6.07e+04
==============================================================================

Notes:
[1] Standard Errors are heteroscedasticity robust (HC0)
[2] The condition number is large, 6.07e+04. This might indicate that there are
strong multicollinearity or other numerical problems.
"""

In [59]:
df_reg2["tp_error"] = df_reg2["tp_error"].abs()
fig = px.scatter(df_reg2,x="is_fifty",y="tp_error")
fig.add_trace(go.Scatter(x=[0,1],y=[0.5831,0.5831-0.0727],name="reg"))
fig.update_xaxes(nticks=2)
fig.update_layout(width=500,title="假說二")

In [70]:
fig = px.imshow(df_reg2[df_reg2.columns[1:]].corr(),text_auto=True ,width=800,height=800)
fig.update_traces(textfont_size=12)

In [71]:
pd.Series([variance_inflation_factor(df_reg2[df_reg2.columns[1:]].astype(float), i)
           for i in range(len(df_reg2.columns[1:]))], index=df_reg2.columns[1:])

momentum       2.018438
Size           7.631658
PE             1.105784
PB             4.328941
turnover       1.749674
implied_ret    1.628592
days           5.544952
is_fifty       2.491054
dtype: float64

TODO: \
共線性

## 假說三：外資持股比例高的公司，外資券商偏向高估股價（高估的預測誤差愈大）


In [60]:
df_reg3 = df_rating_daily_momentum.merge(
    df_holding, how='left', on=[
        '日期', '股票代號', '股票名稱']).dropna()
df_reg3 = pd.concat([df_reg3, in_domestic, df_tp['360天後誤差'], df_implied_ret],
                    axis=1, join='inner')[['360天後誤差', '360日報酬率', '總市值(億)', '本益比', '股價淨值比',
                                           '是否為本土券商', '週轉率(%)',
                                           "隱含報酬率", "外資持股比率"]].dropna()
df_reg3.columns = [
    'tp_error',
    'momentum',
    'Size',
    'PE',
    'PB',
    'Is_foriegn',
    'turnover',
    'implied_ret',
    "foreign_holding"]


In [61]:
df_reg3['Is_foriegn'] = 1 - df_reg3['Is_foriegn']


### 僅篩出看多的報告


In [62]:
df_reg3[df_reg3['implied_ret'] > 0]

tp_error  momentum     Size    PE    PB  Is_foriegn  turnover   
1353  -0.250722 -0.489978    531.5  14.5  1.01         1.0       0.7  \
1354   0.774160 -0.412314    698.3  11.4  1.19         0.0      1.63   
1355   0.503842 -0.431618    716.6  11.7  1.23         1.0      1.44   
1356   0.624770 -0.431618    716.6  11.7  1.23         1.0      1.44   
1357   0.514042 -0.408193    701.3  11.5   1.2         1.0       0.9   
...         ...       ...      ...   ...   ...         ...       ...   
23041  0.347639 -0.368073   7511.5  11.0   2.1         0.0      0.19   
23042  0.109821 -0.368073   7511.5  11.0   2.1         1.0      0.19   
23043  0.228730 -0.250157   4946.9  11.4  1.35         0.0      0.07   
23044  0.397185  0.769173   2688.7  13.8  1.96         0.0      1.41   
23045  0.282703  -0.63585  14549.1  13.8  3.66         0.0       0.3   

       implied_ret  foreign_holding  
1353      0.079537           0.3763  
1354      1.781414           0.3673  
1355      1.259483            0.363  
1356      1.397105            0.363  
1357      1.149047           0.3628  
...            ...              ...  
23041     0.241637           0.3757  
23042     0.022525           0.3757  
23043     0.132081           0.3558  
23044     0.287286           0.4008  
23045     0.136364           0.6706  

[19702 rows x 9 columns]

In [63]:
model3 = smf.ols("tp_error ~ np.log(Size) + PE + PB + Is_foriegn + turnover + momentum + implied_ret + foreign_holding + Is_foriegn*foreign_holding",
                 data=df_reg3[df_reg3['implied_ret'] > 0].astype(np.float64))


In [64]:
result3 = model3.fit(cov_type="HC0")
result3.summary()


<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:               tp_error   R-squared:                       0.456
Model:                            OLS   Adj. R-squared:                  0.456
Method:                 Least Squares   F-statistic:                     402.4
Date:                Sun, 28 May 2023   Prob (F-statistic):               0.00
Time:                        22:31:04   Log-Likelihood:                -9844.4
No. Observations:               19702   AIC:                         1.971e+04
Df Residuals:                   19692   BIC:                         1.979e+04
Df Model:                           9                                         
Covariance Type:                  HC0                                         
==============================================================================================
                                 coef    std err          z      P>|z|      [0.025      0.975]
----------------------------------------------------------------------------------------------
Intercept                      0.0094      0.028      0.339      0.735      -0.045       0.064
np.log(Size)                  -0.0239      0.003     -9.248      0.000      -0.029      -0.019
PE                            -0.0001   8.47e-05     -1.422      0.155      -0.000    4.56e-05
PB                            -0.0002      0.001     -0.141      0.888      -0.003       0.003
Is_foriegn                    -0.0178      0.015     -1.227      0.220      -0.046       0.011
turnover                      -0.0218      0.003     -7.319      0.000      -0.028      -0.016
momentum                       0.1770      0.012     14.969      0.000       0.154       0.200
implied_ret                    0.6389      0.016     39.758      0.000       0.607       0.670
foreign_holding                0.0029      0.021      0.137      0.891      -0.039       0.045
Is_foriegn:foreign_holding    -0.0020      0.030     -0.065      0.948      -0.061       0.057
==============================================================================
Omnibus:                     2649.322   Durbin-Watson:                   1.115
Prob(Omnibus):                  0.000   Jarque-Bera (JB):            27022.861
Skew:                          -0.286   Prob(JB):                         0.00
Kurtosis:                       8.709   Cond. No.                         483.
==============================================================================

Notes:
[1] Standard Errors are heteroscedasticity robust (HC0)
"""

In [65]:
df_plot3 = df_reg3[df_reg3['implied_ret'] > 0]

In [66]:
df_plot3

tp_error  momentum     Size    PE    PB  Is_foriegn  turnover   
1353  -0.250722 -0.489978    531.5  14.5  1.01         1.0       0.7  \
1354   0.774160 -0.412314    698.3  11.4  1.19         0.0      1.63   
1355   0.503842 -0.431618    716.6  11.7  1.23         1.0      1.44   
1356   0.624770 -0.431618    716.6  11.7  1.23         1.0      1.44   
1357   0.514042 -0.408193    701.3  11.5   1.2         1.0       0.9   
...         ...       ...      ...   ...   ...         ...       ...   
23041  0.347639 -0.368073   7511.5  11.0   2.1         0.0      0.19   
23042  0.109821 -0.368073   7511.5  11.0   2.1         1.0      0.19   
23043  0.228730 -0.250157   4946.9  11.4  1.35         0.0      0.07   
23044  0.397185  0.769173   2688.7  13.8  1.96         0.0      1.41   
23045  0.282703  -0.63585  14549.1  13.8  3.66         0.0       0.3   

       implied_ret  foreign_holding  
1353      0.079537           0.3763  
1354      1.781414           0.3673  
1355      1.259483            0.363  
1356      1.397105            0.363  
1357      1.149047           0.3628  
...            ...              ...  
23041     0.241637           0.3757  
23042     0.022525           0.3757  
23043     0.132081           0.3558  
23044     0.287286           0.4008  
23045     0.136364           0.6706  

[19702 rows x 9 columns]

In [67]:
df_plot3.loc[:,"is_foriegn*foreign_holding"]  = df_plot3["Is_foriegn"] * df_plot3["foreign_holding"]
df_plot3 = df_plot3[df_plot3["tp_error"] < 11]

/var/folders/xq/syr6491s2dz4hc1nq8wg29hm0000gn/T/ipykernel_76280/370569417.py:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [68]:
x = np.arange(0,1,0.01)
fig = px.scatter(df_plot3,x="is_foriegn*foreign_holding",y="tp_error")
fig.add_trace(go.Scatter(x=x,y=(x*(-0.002) + 0.0094),name="reg"))
# fig.update_xaxes(nticks=2)
fig.update_layout(width=500,title="假說三")

In [73]:
fig = px.imshow(df_reg3[df_reg3.columns[1:]].corr(),text_auto=True ,width=800,height=800)
fig.update_traces(textfont_size=12)

In [94]:
pd.Series([variance_inflation_factor(df_plot3[df_plot3.columns[1:]].astype(float), i)
           for i in range(len(df_plot3.columns[1:]))], index=df_plot3.columns[1:])

momentum                      1.707654
Size                          1.376422
PE                            1.280148
PB                            3.175172
Is_foriegn                    7.492559
turnover                      1.440745
implied_ret                   2.229937
foreign_holding               5.250382
is_foriegn*foreign_holding    8.284352
dtype: float64